# Test avec CatBoostRegressor

In [4]:
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from catboost import CatBoostRegressor

In [5]:
df = pd.read_csv("../data/silver.csv")

In [6]:
# column_titles = df.columns.tolist()
# column_titles

In [7]:
X = df.drop(["prix_median"], axis=1)
y = df['prix_median']
X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.8, shuffle=True, random_state=42)

categorial_features = ["proximité_autoroute", "riviere"]

numerical_features = ['tx_crim', 'tx_residence','tx_commerce',
       'tx_nitriq', 'nb_piece', 'tx_ancienneté_parc_immo', 'distance_centre_emploi',
        'indice_impot_foncier',  'ratio_eleve_enseignant', 'tx_person_couleur',  'tx_status_sociaux_eco_inf']

categorical_transformer = OneHotEncoder(sparse_output=True)
numerical_transformer = StandardScaler()

preprocessor = ColumnTransformer(
    transformers=[
        ('cat', categorical_transformer, categorial_features),
        ('num', numerical_transformer, numerical_features)
    ],
    remainder="passthrough" 
)

# Créer un objet CatBoostRegressor
# cb_reg = CatBoostRegressor(random_state=42, verbose=False)
cb_reg = CatBoostRegressor(depth=4, learning_rate=0.19293408926881367, l2_leaf_reg=1.9445149121337306, random_state=42, verbose=False)


# Créer un pipeline avec le préprocesseur et le modèle CatBoostRegressor
pipe = Pipeline([
     ('preprocessor', preprocessor),
     ('cb_reg', cb_reg)
])

# Entraîner le pipeline sur les données d'entraînement
pipe.fit(X_train, y_train)
y_pred_train = pipe.predict(X_train)
y_pred_test = pipe.predict(X_test)

print("######## Mean squared error : ")
print("TRAIN :",mean_squared_error(y_train, y_pred_train))
print("TEST :",mean_squared_error(y_test, y_pred_test))
print("/////////////////////////////////////////////////////")

print("######## Mean absolute error : ")
print("TRAIN :",mean_absolute_error(y_train, y_pred_train))
print("TEST :",mean_absolute_error(y_test, y_pred_test))
print("/////////////////////////////////////////////////////")

print("######## R2 score : ")    
print("TRAIN :",r2_score(y_train, y_pred_train))
print("TEST :",r2_score(y_test, y_pred_test))

######## Mean squared error : 
TRAIN : 2273.6718219466316
TEST : 7249155.682021943
/////////////////////////////////////////////////////
######## Mean absolute error : 
TRAIN : 37.551516305714834
TEST : 1868.8373758390314
/////////////////////////////////////////////////////
######## R2 score : 
TRAIN : 0.9999738277571544
TEST : 0.9011484834189751


### Optuna (recherche des hyperparametres)

In [8]:
import optuna
from sklearn.metrics import r2_score

In [9]:
def objective(trial):
    # Définition des hyperparamètres à optimiser
    iterations = trial.suggest_int('iterations', 100, 1000, step=100)
    learning_rate = trial.suggest_float('learning_rate', 0.001, 0.1, log=True)
    depth = trial.suggest_int('depth', 3, 10)
    loss_function = trial.suggest_categorical('loss_function', ['RMSE', 'MAE'])
    subsample = trial.suggest_float('subsample', 0.1, 1.0, step=0.1)
    l2_leaf_reg = trial.suggest_float('l2_leaf_reg', 0.1, 10.0)
    random_strength = trial.suggest_float('random_strength', 0.1, 10.0)
    
    # Création du modèle avec les hyperparamètres suggérés
    model = CatBoostRegressor(iterations=iterations,
                              learning_rate=learning_rate,
                              depth=depth,
                              loss_function=loss_function,
                              subsample=subsample,
                              l2_leaf_reg=l2_leaf_reg,
                              random_strength=random_strength,
                              random_state=42)
    
    # Entraînement du modèle
    model.fit(X_train, y_train)
    
    # Prédiction sur les données de test
    y_pred = model.predict(X_test)
    
    # Calcul du score R2
    r2 = r2_score(y_test, y_pred)
    
    return r2

In [10]:
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=100)

[I 2023-06-12 15:33:34,002] A new study created in memory with name: no-name-9e4f7bc9-e2dd-4956-8f65-d68f5d81f4dc


0:	learn: 6592.7521255	total: 6.88ms	remaining: 6.18s
1:	learn: 6502.2520056	total: 12.9ms	remaining: 5.77s
2:	learn: 6430.5037014	total: 18.8ms	remaining: 5.62s
3:	learn: 6352.5008852	total: 25.6ms	remaining: 5.73s
4:	learn: 6275.0345698	total: 32.6ms	remaining: 5.83s
5:	learn: 6179.6916226	total: 39.8ms	remaining: 5.93s
6:	learn: 6112.8247105	total: 46.3ms	remaining: 5.91s
7:	learn: 6049.1753337	total: 51.6ms	remaining: 5.76s
8:	learn: 5966.3800577	total: 57.6ms	remaining: 5.7s
9:	learn: 5890.8116380	total: 64.3ms	remaining: 5.72s
10:	learn: 5842.7675268	total: 67.8ms	remaining: 5.48s
11:	learn: 5787.1634955	total: 73.7ms	remaining: 5.45s
12:	learn: 5722.8402122	total: 76.7ms	remaining: 5.23s
13:	learn: 5660.7640881	total: 84.3ms	remaining: 5.33s
14:	learn: 5595.2059727	total: 91.3ms	remaining: 5.39s
15:	learn: 5545.8379560	total: 97.7ms	remaining: 5.4s
16:	learn: 5489.8352639	total: 104ms	remaining: 5.41s
17:	learn: 5430.3244140	total: 110ms	remaining: 5.4s
18:	learn: 5352.5903359	t

[I 2023-06-12 15:33:39,170] Trial 0 finished with value: 0.8126525946801714 and parameters: {'iterations': 900, 'learning_rate': 0.01846819944414056, 'depth': 9, 'loss_function': 'MAE', 'subsample': 0.6, 'l2_leaf_reg': 9.650227926851908, 'random_strength': 9.237087830285732}. Best is trial 0 with value: 0.8126525946801714.


898:	learn: 381.7162776	total: 4.94s	remaining: 5.5ms
899:	learn: 380.8680501	total: 4.95s	remaining: 0us
0:	learn: 6658.8481642	total: 651us	remaining: 325ms
1:	learn: 6628.3103153	total: 1.29ms	remaining: 322ms
2:	learn: 6606.5307780	total: 1.76ms	remaining: 292ms
3:	learn: 6578.3971571	total: 2.19ms	remaining: 271ms
4:	learn: 6553.2254456	total: 2.59ms	remaining: 257ms
5:	learn: 6526.7259694	total: 3.02ms	remaining: 249ms
6:	learn: 6499.4083236	total: 3.43ms	remaining: 242ms
7:	learn: 6470.4034932	total: 4.07ms	remaining: 250ms
8:	learn: 6442.3486894	total: 4.45ms	remaining: 243ms
9:	learn: 6419.1487837	total: 4.9ms	remaining: 240ms
10:	learn: 6391.6861561	total: 5.55ms	remaining: 247ms
11:	learn: 6374.3345382	total: 5.99ms	remaining: 243ms
12:	learn: 6346.9650686	total: 6.41ms	remaining: 240ms
13:	learn: 6321.1054802	total: 7.14ms	remaining: 248ms
14:	learn: 6304.0291367	total: 7.52ms	remaining: 243ms
15:	learn: 6282.9048118	total: 8ms	remaining: 242ms
16:	learn: 6258.9268163	total

[I 2023-06-12 15:33:39,444] Trial 1 finished with value: 0.7402217688376267 and parameters: {'iterations': 500, 'learning_rate': 0.0064007512524511, 'depth': 4, 'loss_function': 'MAE', 'subsample': 1.0, 'l2_leaf_reg': 2.820515466473128, 'random_strength': 1.299168489052419}. Best is trial 0 with value: 0.8126525946801714.


...

515:	learn: 708.6408609	total: 409ms	remaining: 146ms
516:	learn: 708.2346414	total: 410ms	remaining: 145ms
517:	learn: 707.7863660	total: 411ms	remaining: 144ms
518:	learn: 705.6149220	total: 412ms	remaining: 144ms
519:	learn: 703.8181379	total: 413ms	remaining: 143ms
520:	learn: 702.8945024	total: 413ms	remaining: 142ms
521:	learn: 701.0867772	total: 414ms	remaining: 141ms
522:	learn: 700.2622490	total: 415ms	remaining: 140ms
523:	learn: 699.2715683	total: 416ms	remaining: 140ms
524:	learn: 697.7769527	total: 416ms	remaining: 139ms
525:	learn: 695.6736591	total: 417ms	remaining: 138ms
526:	learn: 694.4267998	total: 418ms	remaining: 137ms
527:	learn: 693.0892074	total: 419ms	remaining: 136ms
528:	learn: 690.9853165	total: 419ms	remaining: 136ms
529:	learn: 688.5530635	total: 420ms	remaining: 135ms
530:	learn: 685.9558650	total: 421ms	remaining: 134ms
531:	learn: 684.7524554	total: 422ms	remaining: 133ms
532:	learn: 683.0214757	total: 423ms	remaining: 133ms
533:	learn: 681.4668627	tota

[I 2023-06-12 15:35:11,609] Trial 98 finished with value: 0.9053159180939548 and parameters: {'iterations': 700, 'learning_rate': 0.05723913616572793, 'depth': 4, 'loss_function': 'RMSE', 'subsample': 0.30000000000000004, 'l2_leaf_reg': 1.1686599756862974, 'random_strength': 0.44463554486386786}. Best is trial 84 with value: 0.9138190524408446.


451:	learn: 1259.2147265	total: 173ms	remaining: 94.7ms
452:	learn: 1258.0504540	total: 173ms	remaining: 94.4ms
453:	learn: 1255.9056965	total: 174ms	remaining: 94ms
454:	learn: 1254.6601196	total: 174ms	remaining: 93.6ms
455:	learn: 1252.8470794	total: 174ms	remaining: 93.3ms
456:	learn: 1251.3165689	total: 175ms	remaining: 92.9ms
457:	learn: 1250.4288374	total: 175ms	remaining: 92.5ms
458:	learn: 1248.3956798	total: 175ms	remaining: 92.1ms
459:	learn: 1246.7624513	total: 176ms	remaining: 91.8ms
460:	learn: 1244.0552792	total: 176ms	remaining: 91.4ms
461:	learn: 1243.0629705	total: 177ms	remaining: 91ms
462:	learn: 1242.0520232	total: 177ms	remaining: 90.6ms
463:	learn: 1240.1705661	total: 177ms	remaining: 90.2ms
464:	learn: 1236.9654240	total: 178ms	remaining: 89.8ms
465:	learn: 1235.0783662	total: 178ms	remaining: 89.4ms
466:	learn: 1233.7915588	total: 179ms	remaining: 89.1ms
467:	learn: 1232.7821752	total: 179ms	remaining: 88.7ms
468:	learn: 1231.8814344	total: 179ms	remaining: 88.

[I 2023-06-12 15:35:12,340] Trial 99 finished with value: 0.8854721555854284 and parameters: {'iterations': 800, 'learning_rate': 0.09039215525972258, 'depth': 6, 'loss_function': 'RMSE', 'subsample': 0.2, 'l2_leaf_reg': 1.105980834959432, 'random_strength': 1.3773697381094792}. Best is trial 84 with value: 0.9138190524408446.


760:	learn: 217.1784481	total: 579ms	remaining: 29.7ms
761:	learn: 216.4623102	total: 580ms	remaining: 28.9ms
762:	learn: 216.1401611	total: 581ms	remaining: 28.2ms
763:	learn: 215.6601780	total: 582ms	remaining: 27.4ms
764:	learn: 214.5270845	total: 583ms	remaining: 26.7ms
765:	learn: 213.6464391	total: 584ms	remaining: 25.9ms
766:	learn: 213.4308642	total: 584ms	remaining: 25.1ms
767:	learn: 213.2989031	total: 585ms	remaining: 24.4ms
768:	learn: 212.7629730	total: 586ms	remaining: 23.6ms
769:	learn: 212.3141715	total: 586ms	remaining: 22.8ms
770:	learn: 212.0467472	total: 587ms	remaining: 22.1ms
771:	learn: 211.8264765	total: 588ms	remaining: 21.3ms
772:	learn: 211.4746675	total: 589ms	remaining: 20.6ms
773:	learn: 210.4607452	total: 589ms	remaining: 19.8ms
774:	learn: 210.1156887	total: 590ms	remaining: 19ms
775:	learn: 209.4733460	total: 591ms	remaining: 18.3ms
776:	learn: 209.1461727	total: 592ms	remaining: 17.5ms
777:	learn: 208.4544788	total: 592ms	remaining: 16.8ms
778:	learn: 

In [11]:
best_params = study.best_params
best_value = study.best_value

In [12]:
print(best_params)
print(best_value)

{'iterations': 700, 'learning_rate': 0.0693060439562983, 'depth': 6, 'loss_function': 'RMSE', 'subsample': 0.30000000000000004, 'l2_leaf_reg': 0.9500743944149637, 'random_strength': 0.10292853111379426}
0.9138190524408446
